<a href="https://colab.research.google.com/github/RyanTokManMokMTM/NLP_Training2/blob/main/web_crawler.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import requests
from bs4 import BeautifulSoup
HEADER = {
       'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_13_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36'
}


type_list = {
    "playing":"/movie_intheaters.html",
    "upcoming":"/movie_comingsoon.html",
    "thisweek":"/movie_thisweek.html"
}



# Now everything is ready,make each process as a fucnction

In [ ]:

def getAllMovie(movieURL):
  #get detail info with 
  reqDetail = requests.get(movieURL,headers=HEADER)
  detailSoup = BeautifulSoup(reqDetail.text)
  detailSoup = detailSoup.find("div",id="content_l")

  #getting the basic 
  # detailSoup.find("div",class_="movie_intro_info_r")
  info = detailSoup.find("div",class_="movie_intro_info_r")
  # print("Name",info.find("h1").text.strip())
  currentData["MovieName"] = info.find("h1").text.strip()

  #getting movie genre
  genreList = info.findAll("div",class_="level_name")
  genresList = []
  for genre in genreList:
    genresList.append(genre.find("a",class_="gabtn").text.strip())
  currentData["genre"] = ",".join(genresList)

  release = info.findAll("span")[0].text
  currentData["releaseDate"] = release.split("上映日期：")[1].strip()
  
  #getting movie intro
  intro = detailSoup.find("div",class_="gray_infobox_inner")
  introData = intro.find("span",id="story").text.strip()
  currentData["intro"] = introData


In [ ]:

def getAllRelateMovieURL(movieURL):
  #check current movie is visted or not
  if(movieURL in movieLinkVisied): # not None ,movie is already visted
    return

  movieLinkVisied.add(movieURL) #set is now visting and 
  #get detail info with 
  reqDetail = requests.get(movieURL,headers=HEADER)
  detailSoup = BeautifulSoup(reqDetail.text)
  detailSoup = detailSoup.find("div",id="content_l")

  #getting the basic 
  # detailSoup.find("div",class_="movie_intro_info_r")
  info = detailSoup.find("div",class_="movie_intro_info_r")
  # print("Name",info.find("h1").text.strip())
  currentData["MovieName"] = info.find("h1").text.strip()

  #getting movie genre
  genreList = info.findAll("div",class_="level_name")
  genresList = []
  for genre in genreList:
    genresList.append(genre.find("a",class_="gabtn").text.strip())
  currentData["genre"] = ",".join(genresList)

  release = info.findAll("span")[0].text
  currentData["releaseDate"] = release.split("上映日期：")[1].strip()
  
  #getting movie intro
  intro = detailSoup.find("div",class_="gray_infobox_inner")
  introData = intro.find("span",id="story").text.strip()
  currentData["intro"] = introData

  if(detailSoup.findAll("div",class_="l_box have_arbox _c")[0].find("ul","trailer_list alist starlist") != None):
      actorList = detailSoup.findAll("div",class_="l_box have_arbox _c")[0].find("ul","trailer_list alist starlist").findAll("li")
      for actor in actorList:
        # currentActor = actor.find("a",class_="gabtn").find("div",class_="actor_inner").find("h2").text.strip()
        currentActorLink = actor.find("a",class_="gabtn")["href"]
        getActorMovieInfo(currentActorLink) # this action will append all none visited movie of current movie action had-----------------------------------------------------------------------------------------------------------------------------------------\n")

#Working
def getActorMovieInfo(actorURL):
  #check current Actor is already visted
  if(actorURL in actorLinkVisted): #Not None: is already visited
    return

  actorPage = requests.get(actorURL,headers=HEADER)
  actorSoup = BeautifulSoup(actorPage.text)

  actorLinkVisted.add(actorURL)

  #condition is there is any actor?
  if(actorSoup.find("ul",class_="trailer_list _slickfive") != None):
    for movie in actorSoup.find("ul",class_="trailer_list _slickfive").findAll("li"):
        url = movie.find("div",class_="_slickcontent").find("a",class_="gabtn")['href']
        if(url in movieLinkVisied): # not None ,movie is already visted
          continue
        movieUrlList.append(url)

In [ ]:

def webCrawler(baseURL,movieType,pages=1):
  #need some error handle here

  for page in range(1,pages + 1):
    webURL = baseURL + "/"+ movieType +"?page=%s" %page

    #now sending the request
    movieReq = requests.get(webURL,headers=HEADER)
    currentPage = BeautifulSoup(movieReq.text)

    #check current page is empty/no movie there
    if(currentPage.find("div",class_="release_box").find("ul",class_="release_list").find("a",class_="btn_s_introduction") == None):
      return

    movieList = currentPage.find("div",class_="release_box").find("ul",class_="release_list").find("a",class_="btn_s_introduction")['href']

    movieData = currentPage.findAll("div",class_="release_info")
    for item in movieData:
        # get movie name
        # print(item.find("div",class_="release_movie_name").find("a",class_="gabtn").text.strip())

        #get movie detail URL,all detail 
        # print(item.find("div",class_="release_btn color_btnbox").find("a",class_="btn_s_introduction")["href"])
        detailURL = item.find("div",class_="release_btn color_btnbox").find("a",class_="btn_s_introduction")["href"]
        movieUrlList.append(detailURL)

In [ ]:
movieUrlList = []
actorLinkVisted = set()
movieLinkVisied = set()
currentData = {}


webCrawler("https://movies.yahoo.com.tw",type_list["playing"],1)
webCrawler("https://movies.yahoo.com.tw",type_list["upcoming"],7)
webCrawler("https://movies.yahoo.com.tw",type_list["thisweek"],7)


In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
#now will loop over the current list and add new item via its actor
import csv
#add to csv every 5 time
for i in movieUrlList:
    getAllRelateMovieURL(i)

In [ ]:
lists = []
def getAll(movieUriList):
  #check current movie is visted or not
  #get detail info with 
  for i in movieUriList:
    reqDetail = requests.get(i,headers=HEADER)
    detailSoup = BeautifulSoup(reqDetail.text)
    detailSoup = detailSoup.find("div",id="content_l")

    data = {}
    #getting the basic 
    # detailSoup.find("div",class_="movie_intro_info_r")
    info = detailSoup.find("div",class_="movie_intro_info_r")
    # print("Name",info.find("h1").text.strip())
    data["MovieName"] = info.find("h1").text.strip()

    #getting movie genre
    genreList = info.findAll("div",class_="level_name")
    genresList = []
    for genre in genreList:
      genresList.append(genre.find("a",class_="gabtn").text.strip())
    data["genre"] = ",".join(genresList)

    release = info.findAll("span")[0].text
    data["releaseDate"] = release.split("上映日期：")[1].strip()
    
    #getting movie intro
    intro = detailSoup.find("div",class_="gray_infobox_inner")
    introData = intro.find("span",id="story").text.strip()
    data["intro"] = introData
    lists.append(data)
    print(data)

In [ ]:
getAll(movieUrlList)

Streaming output truncated to the last 5000 lines.
{'MovieName': '人面魚 紅衣小女孩外傳', 'genre': '劇情,恐怖,懸疑/驚悚', 'releaseDate': '2018-11-23', 'intro': '★ 台灣真實靈異「人面魚」鄉野傳說改編！紅衣魔神仔三部曲最終章！\r\n★ 國片影史破億恐怖片《紅衣小女孩》系列外傳電影，原班團隊打造更駭人的魔神仔宇宙！\r\n\xa0\r\n刑事組警官阿忠（張書偉 飾）帶著一樁離奇的滅門血案找上虎爺乩身志成（鄭人碩 飾），志成決定對兇嫌執行驅魔儀式「炸魔神仔」，未料棄置的吳郭魚屍嘴中竟吐出一條遭附身的小魚，被男孩家豪（吳至璿 飾）撿回家飼養。一連串的怪事隨即開始發生，母親雅惠（徐若瑄 飾）更是舉止怪異，陷入瘋狂。為拯救母親，家豪向虎爺求救，他們原以為化解了人面魚的怨念就能阻止這一切，沒想到更難解的仇恨，正潛伏在森林裡等著他們…。《人面魚 紅衣小女孩外傳》將於11月23日正式上映！更多電影資訊歡迎上官方粉絲團查詢：https://www.facebook.com/tagalongmovie。'}
{'MovieName': '寒蟬效應', 'genre': '劇情', 'releaseDate': '2014-10-24', 'intro': '★入圍釜山影展新潮流競賽單元★四大女星 極致演技 驚艷影壇《寒蟬效應》描寫四個背景不同的女人，因一個事件相聚，面對了愛情的種種紛爭與愛情裡的殘酷 … 隨著事件的落幕，四個人展現的勇敢與成長的故事： 都會女孩白白（郭采潔 飾）來到東部大學攻讀音樂研究所，很快就認識個性純真的同學木宏(黃遠 飾)並順利加入學校樂團演奏，在與木宏快樂相處的同時，意外捲入與指導老師（戴立忍 飾）的情感陷阱中無法自拔。 這個事件將多年后不見后的三個女強人：方律師（徐若瑄 飾）、林律師（賈靜雯 飾）與王老師（周幼婷 飾）聚在一起。 各自在不同領域發展的昔日同學與校友，為了這樁情感糾葛事件，陷入一場在情感裡的信任、背叛與正義的風暴……'}
{'MovieName': '聽見下雨的聲音', 'genre': '愛情,音樂/歌舞', 'releaseDate': '2013-10-04', 'intro': '下雨天，有人說是天空在哭泣，也有人

In [79]:
print(len(set(movieUrlList)))


MovieName  ...                                              intro
0              路卡的夏天  ...  皮克斯全新原創《路卡的夏天》，故事背景發生在美麗的義大利濱海小鎮里維埃拉，一位名叫路卡的海怪...
1                薄荷糖  ...  ★韓國重量級名導李滄東「綠色三部曲」之一！ \r\n★勇奪「南韓奧斯卡」大鐘獎最佳影片、導演...
2                 人聲  ...  一個焦慮的女人等著要跟她分手的男人可以出現，取回他的行李，心裡有著一絲絲盼望，也許可以有轉圜...
3      雙面薇若妮卡 經典數位修復  ...  ★ 1991坎城影展最佳女主角、國際影評人費比西獎、人道主義精神獎\r\n★ 1992 金球...
4               合法伴侶  ...  ★英國倫敦的異國追愛故事！無論是男女戀，還是男男戀？結婚才是合法，敢登記才是真愛\r\n★台...
...              ...  ...                                                ...
10466   夏天的故事 經典數位修復  ...  「我看似容易被追到手，卻對感情要求嚴苛。我要求全心全意，對方也得是。」\r\n \r\n夏天...
10467           感謝上帝  ...  亞歷山大事業有成，家庭美滿，他有深愛他的嬌妻，還是五個小孩的爸爸。某天，他偶然得知當年曾經性...
10468          雙面勞倫斯  ...  ★坎城影展同志金棕櫚獎   一種注目單元最佳女主角 ★多倫多影展 最佳加拿大劇情片★《聽媽媽...
10469       屬於我們的聖誕節  ...  ★奇蹟！感動！【屬於我們的聖誕節】榮獲坎城影展61週年特別獎一場愛與秘密的燭光盛宴…她趁假期...
10470           全面霾伏  ...  ★繼《明天過後》、《加州大地震》、《氣象戰》後，又一年度災難懸疑動作鉅獻！\r\n★全新空污...

[10471 rows x 4 columns]